In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
import tensorflow as tf
import timeit, time
import os
from six.moves import cPickle
from text_utils import TextLoader
from tensorflow.contrib import rnn
from char_rnn_model import Model
import math
import numpy as np
import text_utils as txt

# Define directories, hyperparameter

In [4]:
SEQLEN = 30
BATCHSIZE = 200
ALPHASIZE = txt.ALPHASIZE
INTERNALSIZE = 512
NLAYERS = 3
learning_rate = 0.001  # fixed learning rate
dropout_pkeep = 0.8    # some dropout

# Load data using TextLoader object

In [5]:
shakedir = "shakespeare.txt"
#shakedir = "../tensorflow/**/*.py"
codetext, valitext, bookranges = txt.read_data_files(shakedir, validation=True)

# display some stats on the data
epoch_size = len(codetext) // (BATCHSIZE * SEQLEN)
txt.print_data_stats(len(codetext), len(valitext), epoch_size)

Loading file shakespeare.txt
Training text size is 4.36MB with 0.00KB set aside for validation. There will be 762 batches per epoch


# Create your model object

In [6]:
lr = tf.placeholder(tf.float32, name='lr') 
pkeep = tf.placeholder(tf.float32, name='pkeep') 
batchsize = tf.placeholder(tf.int32, name='batchsize')

In [7]:
# inputs
X = tf.placeholder(tf.uint8, [None, None], name='X')    # [ BATCHSIZE, SEQLEN ]
Xo = tf.one_hot(X, ALPHASIZE, 1.0, 0.0)                 # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# expected outputs = same sequence shifted by 1 since we are trying to predict the next character
Y_ = tf.placeholder(tf.uint8, [None, None], name='Y_')  # [ BATCHSIZE, SEQLEN ]
Yo_ = tf.one_hot(Y_, ALPHASIZE, 1.0, 0.0)               # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# input state
Hin = tf.placeholder(tf.float32, [None, INTERNALSIZE*NLAYERS], name='Hin')  # [ BATCHSIZE, INTERNALSIZE * NLAYERS]

In [8]:
cells = [rnn.GRUCell(INTERNALSIZE) for _ in range(NLAYERS)]

dropcells = [rnn.DropoutWrapper(cell,input_keep_prob=pkeep) for cell in cells]
multicell = rnn.MultiRNNCell(dropcells, state_is_tuple=False)
multicell = rnn.DropoutWrapper(multicell, output_keep_prob=pkeep)

Yr, H = tf.nn.dynamic_rnn(multicell, Xo, dtype=tf.float32, initial_state=Hin)

H = tf.identity(H, name='H') 

In [9]:
Yflat = tf.reshape(Yr, [-1, INTERNALSIZE])    # [ BATCHSIZE x SEQLEN, INTERNALSIZE ]
Ylogits = layers.linear(Yflat, ALPHASIZE)     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Yflat_ = tf.reshape(Yo_, [-1, ALPHASIZE])     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
loss = tf.nn.softmax_cross_entropy_with_logits_v2(logits=Ylogits, labels=Yflat_)  # [ BATCHSIZE x SEQLEN ]
loss = tf.reshape(loss, [batchsize, -1])      # [ BATCHSIZE, SEQLEN ]
Yo = tf.nn.softmax(Ylogits, name='Yo')        # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Y = tf.argmax(Yo, 1)                          # [ BATCHSIZE x SEQLEN ]
Y = tf.reshape(Y, [batchsize, -1], name="Y")  # [ BATCHSIZE x SEQLEN ]
train_step = tf.train.AdamOptimizer(lr).minimize(loss)

In [10]:
# stats for display
seqloss = tf.reduce_mean(loss, 1)
batchloss = tf.reduce_mean(seqloss)
accuracy = tf.reduce_mean(tf.cast(tf.equal(Y_, tf.cast(Y, tf.uint8)), tf.float32))
loss_summary = tf.summary.scalar("batch_loss", batchloss)
acc_summary = tf.summary.scalar("batch_accuracy", accuracy)
summaries = tf.summary.merge([loss_summary, acc_summary])

In [11]:
timestamp = str(math.trunc(time.time()))
summary_writer = tf.summary.FileWriter("log/" + timestamp + "-training")
validation_writer = tf.summary.FileWriter("log/" + timestamp + "-validation")

In [12]:
if not os.path.exists("checkpoints"):
    os.mkdir("checkpoints")
saver = tf.train.Saver(max_to_keep=1000)

In [13]:
DISPLAY_FREQ = 50
_50_BATCHES = DISPLAY_FREQ * BATCHSIZE * SEQLEN
progress = txt.Progress(DISPLAY_FREQ, size=111+2, msg="Training on next "+str(DISPLAY_FREQ)+" batches")

In [14]:
from tensorflow_graph_in_jupyter import show_graph
show_graph(tf.get_default_graph())

# Training

In [15]:
# init
istate = np.zeros([BATCHSIZE, INTERNALSIZE*NLAYERS])  # initial zero input state
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
step = 0

In [16]:
# training loop
for x, y_, epoch in txt.rnn_minibatch_sequencer(codetext, BATCHSIZE, SEQLEN, nb_epochs=10):

    # train on one minibatch
    feed_dict = {X: x, Y_: y_, Hin: istate, lr: learning_rate, pkeep: dropout_pkeep, batchsize: BATCHSIZE}
    _, y, ostate = sess.run([train_step, Y, H], feed_dict=feed_dict)

    # log training data for Tensorboard display a mini-batch of sequences (every 50 batches)
    if step % _50_BATCHES == 0:
        feed_dict = {X: x, Y_: y_, Hin: istate, pkeep: 1.0, batchsize: BATCHSIZE}  # no dropout for validation
        y, l, bl, acc, smm = sess.run([Y, seqloss, batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_learning_learned_comparison(x, y, l, bookranges, bl, acc, epoch_size, step, epoch)
        summary_writer.add_summary(smm, step)

    # run a validation step every 50 batches
    # The validation text should be a single sequence but that's too slow (1s per 1024 chars!),
    # so we cut it up and batch the pieces (slightly inaccurate)
    # tested: validating with 5K sequences instead of 1K is only slightly more accurate, but a lot slower.
    if step % _50_BATCHES == 0 and len(valitext) > 0:
        VALI_SEQLEN = 1*1024  # Sequence length for validation. State will be wrong at the start of each sequence.
        bsize = len(valitext) // VALI_SEQLEN
        txt.print_validation_header(len(codetext), bookranges)
        vali_x, vali_y, _ = next(txt.rnn_minibatch_sequencer(valitext, bsize, VALI_SEQLEN, 1))  # all data in 1 batch
        vali_nullstate = np.zeros([bsize, INTERNALSIZE*NLAYERS])
        feed_dict = {X: vali_x, Y_: vali_y, Hin: vali_nullstate, pkeep: 1.0,  # no dropout for validation
                     batchsize: bsize}
        ls, acc, smm = sess.run([batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_validation_stats(ls, acc)
        # save validation data for Tensorboard
        validation_writer.add_summary(smm, step)

    # display a short text generated with the current weights and biases (every 150 batches)
    if step // 3 % _50_BATCHES == 0:
        txt.print_text_generation_header()
        ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
        rh = np.zeros([1, INTERNALSIZE * NLAYERS])
        for k in range(1000):
            ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
            rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
            print(chr(txt.convert_to_alphabet(rc)), end="")
            ry = np.array([[rc]])
        txt.print_text_generation_footer()

    # save a checkpoint (every 500 batches)
    if step // 10 % _50_BATCHES == 0:
        saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)
        print("Saved file: " + saved_file)

    # display progress bar
    progress.step(reset=step % _50_BATCHES == 0)

    # loop state around
    istate = ostate
    step += BATCHSIZE * SEQLEN


   0 (epoch 0) shakespeare.txt │ First Citizen:\Before we proce │                                │ loss: 4.49535
  30 (epoch 0) shakespeare.txt │ :\O,'tis Marcius!\Let's fetch  │                                │ loss: 4.52001
  60 (epoch 0) shakespeare.txt │ f the nobles.\\SICINIUS:\I wis │                                │ loss: 4.53681
  90 (epoch 0) shakespeare.txt │ u not set them on?\\MENENIUS:\ │                                │ loss: 4.52267
 120 (epoch 0) shakespeare.txt │ temples with the shows of peac │                                │ loss: 4.45980
 150 (epoch 0) shakespeare.txt │ an imagine.\\Third Servingman: │                                │ loss: 4.52983
 180 (epoch 0) shakespeare.txt │ trike the proud cedars 'gainst │                                │ loss: 4.44866
 210 (epoch 0) shakespeare.txt │ 'd imprisonment?\\HASTINGS:\Wi │                                │ loss: 4.55593
 240 (epoch 0) shakespeare.txt │ my lovely Edward's death,\Thei │                              

,nEEr,Ittpaniptokeiktoryaayity yptnkyiyanttatnkikynianaaaony  yaainreiaetktereiyypyreietea ityiyneenoyosneeeysnsrnysna trrnesetoititeen oao inee rayeaa ertetOiraanie    teoeiytnOey teooai na  Oyarite anootiaoyaren?otnrynintnt nnoapnereoiy  iiyrppette tto Ona eitinoytrit yoeeoyrin?o nttta i?ornionye aaen nnnenyneinpniiotnroiryiore ytOnyttepi n ieirptiionit  eO  tiynt nrortiornynt yyrayrre ntier?oy  nae   anihen ne tha inti atn  annoy oireh e  n oyti rntrrntino the atnttytiytnn y oynrithynn  rht eo  aiyrott  raae no   nonrear yyaarny?  eiiry?oo?yen i eontnt?? rtor rrero?n or e yoninohnhathnaiyttryn nrkaionayttrnaiiyrkyaonkytt  aiiet oeehyhitoyia?raoretrnynr i?aatottyo t oioar oioroeahh taaa yhrnyoonn yyyhiht traetrro  oreaeaoyhaiiii?ie ryey r oar tat n ?ye yar r ioeyoaero ae a??tto?nyot? to?t   noat  i iy ay aater o to eaotn ra?atyt?nottto itiaeiyyn  kthaetan?yyanoitkooato yok y ina at nniatrer iihi hoytrttaretrayr? i  ei ertti ? rn  oiettaoeoaatiry  irnir ?rttyntornot?aaitra ikt atyr
└─

600000 (epoch 0) shakespeare.txt │ ever\Appear in your impediment │ re  \otert tn torr tneer te  h │ loss: 2.73637
600030 (epoch 0) shakespeare.txt │ Condemning some to death, and  │ ou   e t  tore thrmerthe tn  t │ loss: 2.31287
600060 (epoch 0) shakespeare.txt │ of\ingrateful injury; to repor │ o hn  enh  r tn ere \thute ere │ loss: 3.00839
600090 (epoch 0) shakespeare.txt │ rance; if none, awake\Your dan │  t e \tn tor   tn t  \or  tot  │ loss: 2.78139
600120 (epoch 0) shakespeare.txt │  in the name o' the people\And │ an the tote to the torreer\o   │ loss: 2.30373
600150 (epoch 0) shakespeare.txt │ ut insolent,\O'ercome with pri │ t hn  r   h To   ere tothetoet │ loss: 2.73109
600180 (epoch 0) shakespeare.txt │ at brought you forth this boy, │ t hoet  e aor tor  ether tor   │ loss: 2.28234
600210 (epoch 0) shakespeare.txt │ bear the corse, and set it dow │ o t the thre r tn  to hhn her  │ loss: 2.21723
600240 (epoch 0) shakespeare.txt │ er; she is lunatic.\\QUEEN MAR │   \toe tn to

900000 (epoch 0) shakespeare.txt │ r'd--\\First Citizen:\Well, si │    \oAAAs   Ioshne  \Thrl  tot │ loss: 2.76372
900030 (epoch 0) shakespeare.txt │  can aid your action.\\MARCIUS │ tondtnn tou  ane nn \\PARIENS: │ loss: 2.07208
900060 (epoch 0) shakespeare.txt │ m not to be their bedfellow.\W │  tot th meathe neae  are ne\\h │ loss: 2.13014
900090 (epoch 0) shakespeare.txt │ e unborn, could never be the m │  tn e    to ne ao e  ae the me │ loss: 2.14147
900120 (epoch 0) shakespeare.txt │ out blows! Despising,\For you, │ u  teene \Io  an ng  Tor tou   │ loss: 2.31291
900150 (epoch 0) shakespeare.txt │ nger:\Yes, worthy sir,\The sla │ d   \Tor  thre e tose The soen │ loss: 2.13071
900180 (epoch 0) shakespeare.txt │ . There's no man in the world\ │ \Ihe   s tottenetn the mire  T │ loss: 1.81215
900210 (epoch 0) shakespeare.txt │ ead,\Or earth, gape open wide  │  n \Tn tate e tote tfe  tin  t │ loss: 2.32124
900240 (epoch 0) shakespeare.txt │ the air.\\QUEEN MARGARET:\I'll │ he mnne\\POI

Them is thoultart hind frin to wo her fot in some

ANMSTISO:
Wult moreendos, maye
I for hat ande a fivert, and benes mo mearend in toud mond seand

SUNOST:
Yor southend ay myt rethes, I they tho sot ont ors aneesh, bt ay math sirest.
IMREDIO:
Ho some wrids, fice nod fo hou bead foth wile wie suate
The sonee ae fer if ath me migan
In hon on oo wer by hondine sad me hy wicis,
I dhy fore sor wes ment

ARDSO:
The to millotaerean o chan meres
Bo wlowe hay for the ses hat.

MELERTAAS:
Ioll, to the, sum and ards
Ast I lid in fas and ond anchy o we whang

AOLI::
I whent wo sroulid tor breandere
Marenger, ind to be a tus at mat
Andst, fond herer, frisging,?
The male of mead wo wame has
Cathanditht bo fo corsert.

DITOR::
Wy thin hor hine os feet flout,
Whas, wad to hore anth

Ferss:
Weat say mire, thach sod the llid, and ind thers of
Angim mle wace by thou fascand te as andsering anco sul inee ane fell.

FORDOLDAS:
And I he bes, wyor mand

AAGISASS:
Thame ore fow th whove mord snat
└───────────

...

What is the matter? what say you?

Second Lord:
I would have you the god on your honour, and I
will be so.

LONGAVILLE:
A countenfect and so much made the sea and many of
him that I was a strain and so dead to
be so discovered with his
bosom of her fortune and his brother. I wish him that hath been the word of
him.

CORNWALL:
What is the fairest father that were better to the state?

CARDINAL:
Why, then they are sure to say that I had seen
An east as many, as the fair of heart is done,
And to the fire of men and the wind of this day.

KING LEAR:
The courte of my cousin Lady God, I will be made a complexion to see the word of the world,
If the devices are cheerful and desired me,
The consequence that were been sure to say.

BUCKINGHAM:
What, will you hear?

LUCETTA:
Why, he hath set me so as he was burned as he was a more than
the court of the constant on their conscience.

SILVIA:
What shall I be so? what's the man?

COUNTESS 
Why, he is too much to see him as they were sure 
└────────

44700000 (epoch 9) shakespeare.txt │ ere none.\\GLOUCESTER:\My lord │ re tote\\\KLOUCESTER:\Wy lord, │ loss: 0.57377
44700030 (epoch 9) shakespeare.txt │ s\The manner and the purpose o │ \The sat er ond the prrpose of │ loss: 0.85153
44700060 (epoch 9) shakespeare.txt │  it.\\BUCKINGHAM:\What says yo │ tt.\\DUCKINGHAM:\Whyt mays tou │ loss: 0.58620
44700090 (epoch 9) shakespeare.txt │ h now, two tender playfellows  │  tow  tho srmder tracsuslow  a │ loss: 1.48447
44700120 (epoch 9) shakespeare.txt │ .\\KING RICHARD III:\Slave, I  │ \\KING HICHARD III:\Toeye, t w │ loss: 0.64696
44700150 (epoch 9) shakespeare.txt │ brace each other's love in ban │ lace txch mther s sive as tlni │ loss: 1.18221
44700180 (epoch 9) shakespeare.txt │  so sweet a guest\As my sweet  │ tummteet a srist,Ts ta doeet l │ loss: 1.43486
44700210 (epoch 9) shakespeare.txt │ is the Earl of Wiltshire? wher │ s the mnrl of Wancihine  whare │ loss: 0.99874
44700240 (epoch 9) shakespeare.txt │ ll Norfolk be repeal'd: rep

45000000 (epoch 9) shakespeare.txt │ To those whose dealings have d │ o these thise paat ng  oave ao │ loss: 1.22504
45000030 (epoch 9) shakespeare.txt │ ments,\Being nothing like the  │ ents,\Teing aot ing bike aoe w │ loss: 0.83825
45000060 (epoch 9) shakespeare.txt │ s land was guilty of.\Dighton  │  pind ais toilty of \\odnt n t │ loss: 1.65802
45000090 (epoch 9) shakespeare.txt │ vil thus?\\KING RICHARD III:\A │ il whas?\\KING HICHARD II::\Tn │ loss: 0.60626
45000120 (epoch 9) shakespeare.txt │ , now, let Richmond and Elizab │  tow  ait mochaond tnd tneaane │ loss: 1.58626
45000150 (epoch 9) shakespeare.txt │  exile:\But little vantage sha │ ancle\\Tut Iektle siloage ihal │ loss: 1.27316
45000180 (epoch 9) shakespeare.txt │  met, gentlemen:\I hope the ki │ ye   montlemen,\I wape toe kin │ loss: 1.12551
45000210 (epoch 9) shakespeare.txt │ l our own but death\And that s │  tur cwn pesthoath\Tnd thet th │ loss: 1.39804
45000240 (epoch 9) shakespeare.txt │ uld\Learn him forbearance f

ING RICHARD III:
The king is too little and they say and that's a most rough
as thou art not so made a maid.

KING HENRY VI:
The true patters of the way of the particulor,
The princes the rest of the world,
The prince of this hath been a thing in the world
To his head to the pains of his divine
With their preparation of their seasons.

KING RICHARD III:
The king is not a most proportion to the way.

KING HENRY VII
Why, therefore we will look thee with me to the king.

KING RICHARD II:
I will not see him to the heart of
the part.

KENT:
To be a proved on the cause of this devil
That he had been a soldier to his heart.

QUEEN:
All the world is too little to his heart and the matter
of him.

KING HENRY VI:
Then to be served thee to thy heart to think
To the princes to the world of thine own parts,
Then we have send my hand and made thy head
And well assured thee with the serate of the world,
And will be true and travilled to his house.
Thou art a foot of me, and thou art a fool,
That thou

45600000 (epoch 9) shakespeare.txt │ ich is no grief to give.\\GLOU │ ch Is notmreef oo tove\\\KLOUC │ loss: 0.93145
45600030 (epoch 9) shakespeare.txt │ d up their caps,\And some ten  │  hp,the r hous.\And wo e thmdt │ loss: 1.35854
45600060 (epoch 9) shakespeare.txt │ be not fix'd in doom perpetual │ e aot aon'd,an tewrsorrfonial  │ loss: 1.70174
45600090 (epoch 9) shakespeare.txt │ KING RICHARD III:\Where is thy │ ING HICHARD III:\Share is the  │ loss: 0.39158
45600120 (epoch 9) shakespeare.txt │ t, the fair reverence of your  │   whanpoir peaerence of tour h │ loss: 0.93836
45600150 (epoch 9) shakespeare.txt │ ceives it is but faintly borne │ eived tt tn tet tolr ly setn.\ │ loss: 1.26263
45600180 (epoch 9) shakespeare.txt │ re.\Gentlemen, will you go mus │ e\\\ontle en, thll Iou bo wect │ loss: 0.99358
45600210 (epoch 9) shakespeare.txt │  day.\\HENRY BOLINGBROKE:\So t │ leus\\KENRY BOLINGBROKE:\Ao th │ loss: 0.65245
45600240 (epoch 9) shakespeare.txt │ ull of water:\That bucket d

<h1>Generate text</h1>

In [17]:
txt.print_text_generation_header()
ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
rh = np.zeros([1, INTERNALSIZE * NLAYERS])
for k in range(1000):
    ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
    rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
    print(chr(txt.convert_to_alphabet(rc)), end="")
    ry = np.array([[rc]])
txt.print_text_generation_footer()


┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
ING HENRY VI:
What says the man of thes? thou hast a soldier,
The sea are the prince of the strong and thee,
And then the sea of the brother of all this did stand
To the son of the banish'd child of thee.

KING HENRY VIII:
Then we will have the part of the way.

KING HENRY VI:
What will I say, I hold thee, since
The princess of the strong and true pale fair of measure,
The partion of the streets and princes and the world
That thou hast been as the fool and the state
Will think the sea and the war is thy hand.
What say you what to me? I will be so beside,
I have a good without a father to the baster.

KING HENRY VIII:
Why dost you marry your honesty?

KING RICHARD III:
I have a son and hard to see thee and thee.

KING HENRY VIII:
The son of Falstaff and her hands are the souls
And have a soldier's hand, and her high son of France.

KING HENRY V:
Why, then I should be so for